In [1]:
#Step -1 : Imports
import random
import numpy as np
import plotly.graph_objects as go

from IPython.display import Markdown as md

In [3]:
#Step 0 : acquire data

N = 1000 #people
start_cash = 100.00
rounds = 200
people = [[start_cash] for i in range(N)]

if (N%2):
    print "please keep N even"

def func_inv_round(input_people): #a single round of investments
    sN = range(N)
    random.shuffle(sN) #shuffled list to determine wheter profit is positive or negative for a person

    p = random.random() / 2 # percentage market gain/loss this round
    
    for cnt, Pidx in enumerate(sN):
        if  cnt == int(N / 2) :
            p = p*-1 #if halfway shuffled list, the rest loses money
        
        
        personal_p = p * random.random() #personal profit is based on how many % of their wealth is invested #maybe kijken of normal dist beter werkt hier?

        people[Pidx].append(round(people[Pidx][-1] + personal_p*people[Pidx][-1],2)) #add new entry to the persons money record
        
    return input_people #return the list of people with new balances

def func_investments(r): #runs r rounds of investments and plots them
    global people #altering the original variable
    for i in range(r):
        people = func_inv_round(people)
    
    fig = go.Figure()
    for i in range(N):
        fig.add_trace(go.Scatter(x = range(r), y = people[i]))

    fig.show()  
    
func_investments(rounds)


In [ ]:
# Step 1 : log-log plot
def func_powerlaw_t(t, ret=True, plot=False, log=False):
    money_at_t = sorted([people[i][t] for i in range(N)])[::-1]
    if plot:
        fpt_plot = go.Figure()
        fpt_plot.add_trace(go.Scatter(x = range(N), y = money_at_t))
        if log:
            fpt_plot.update_layout(xaxis_type="log", yaxis_type="log")
        fpt_plot.show()
    if ret:
        return money_at_t

func_powerlaw_t(-1, plot=True, ret=False)
func_powerlaw_t(-1, plot=True, log=True, ret=False)


In [ ]:
#Step 2 : Polyfit

def polyfit_data(data):
    x = np.array(range(len(data))) + 1 # Array with same size as data, starting from 1 to avoid pesky divide-by-zero errors
    polynomial_coefficients, residuals = np.polyfit(np.log(x),np.log(data), 1,full=True)[:2] # Returns coefficients of a polynomial of degree 1 (just a linear relation) with least square fit to data
    
    return polynomial_coefficients, residuals

data_last_t = func_powerlaw_t(-1)
polycoeffs, error = polyfit_data(data_last_t)
print polynomial_coefficients, "\n", residuals

In [ ]:
#Step 3 : function

md("the best fitting power law for the log-log plot of the division of wealth is:  \n  \n$$y = e^{} + x^{}$$".format(("{"+str(round(polycoeffs[1],3))+"}"), ("{"+str(round(polycoeffs[0],3))+"}")) )


In [ ]:
polynomial = np.poly1d(polycoeffs)